## Importing the necessary libraries

In [1]:
%matplotlib inline
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import geopandas as gpd
from geopy.geocoders import Nominatim
import folium
from folium import plugins
from sklearn.cluster import KMeans
import matplotlib.cm as cm
import matplotlib.colors as colors
import requests

In [2]:
df = pd.read_csv("london-borough-profile.csv")
df.head()

Code               borough Inner/_Outer_London  \
0  E09000001        City of London        Inner London   
1  E09000002  Barking and Dagenham        Outer London   
2  E09000003                Barnet        Outer London   
3  E09000004                Bexley        Outer London   
4  E09000005                 Brent        Outer London   

   GLA_Population_Estimate_2017  GLA_Household_Estimate_2017  \
0                        8800.0                       5326.0   
1                      209000.0                      78188.0   
2                      389600.0                     151423.0   
3                      244300.0                      97736.0   
4                      332100.0                     121048.0   

   Inland_Area_(Hectares)  Population_density_(per_hectare)_2017  \
0                   290.0                                   30.3   
1                  3611.0                                   57.9   
2                  8675.0                                   44.9   
3                  6058.0                                   40.3   
4                  4323.0                                   76.8   

   Average_Age,_2017  Proportion_of_population_aged_0-15,_2015  \
0               43.2                                      11.4   
1               32.9                                      27.2   
2               37.3                                      21.1   
3               39.0                                      20.6   
4               35.6                                      20.9   

   Proportion_of_population_of_working-age,_2015  ...  \
0                                           73.1  ...   
1                                           63.1  ...   
2                                           64.9  ...   
3                                           62.9  ...   
4                                           67.8  ...   

   Happiness_score_2011-14_(out_of_10)  Anxiety_score_2011-14_(out_of_10)  \
0                                  6.0                                5.6   
1                                  7.1                                3.1   
2                                  7.4                                2.8   
3                                  7.2                                3.3   
4                                  7.2                                2.9   

   Childhood_Obesity_Prevalance_(%)_2015/16  \
0                                       NaN   
1                                      28.5   
2                                      20.7   
3                                      22.7   
4                                      24.3   

   People_aged_17+_with_diabetes_(%)  \
0                                2.6   
1                                7.3   
2                                6.0   
3                                6.9   
4                                7.9   

   Mortality_rate_from_causes_considered_preventable_2012/14  \
0                                                129           
1                                                228           
2                                                134           
3                                                164           
4                                                169           

  Political_control_in_council  \
0                          NaN   
1                          Lab   
2                         Cons   
3                         Cons   
4                          Lab   

   Proportion_of_seats_won_by_Conservatives_in_2014_election  \
0                                                NaN           
1                                                0.0           
2                                               50.8           
3                                               71.4           
4                                                9.5           

  Proportion_of_seats_won_by_Labour_in_2014_election  \
0                                                NaN   
1                                                10

# Visualising London

In [4]:
address = 'London'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of London are {}, {}.'.format(latitude, longitude))

# create map of London using latitude and longitude values
map_London = folium.Map(location=[latitude, longitude], zoom_start=10)


map_London

/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.20.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  This is separate from the ipykernel package so we can avoid doing imports until


The geograpical coordinate of London are 51.5073219, -0.1276474.


# We can't really see the limits of London on the above map, so I've used a geojson file with the outline to demarcate the limits of London

In [5]:
london_outline = 'greaterlondon.json'

In [6]:
address = 'London'

print('The geograpical coordinate of London are {}, {}.'.format(latitude, longitude))

# create map of London using latitude and longitude values
map_London = folium.Map(location=[latitude, longitude], zoom_start=10)
folium.GeoJson(london_outline,
              ).add_to(map_London)

map_London

The geograpical coordinate of London are 51.5073219, -0.1276474.


# In order to be able to tell the difference between boroughs in London, we plot the outline of each borough in London

In [7]:
borough_geo = 'london_boroughs_proper.geojson'

In [8]:
borough_geo = 'london_boroughs_proper.geojson'
address = 'London'

print('The geograpical coordinate of London are {}, {}.'.format(latitude, longitude))

# create map of London using latitude and longitude values
map_London = folium.Map(location=[latitude, longitude], zoom_start=10)
folium.GeoJson(borough_geo,
              ).add_to(map_London)

map_London

The geograpical coordinate of London are 51.5073219, -0.1276474.


In [9]:
borough_df = pd.DataFrame(df.borough)

## Finding the latitiude and longitude values for the head of each borough (i.e.) the location listed with the same name as the borough

In [10]:
borough_df['Latitude'] = 0
borough_df['Longitude'] = 0
borough_df.head()

borough  Latitude  Longitude
0        City of London         0          0
1  Barking and Dagenham         0          0
2                Barnet         0          0
3                Bexley         0          0
4                 Brent         0          0

In [18]:
geolocator = Nominatim()
for i in (range(0,borough_df['borough'].shape[0])):
    address = borough_df.loc[i,'borough'] + ", England"
    location = geolocator.geocode(address, timeout = None)
    if (location != None):
        borough_df.loc[i,'Latitude'] = location.latitude
        borough_df.loc[i,'Longitude'] = location.longitude

print(borough_df.shape)
borough_df.head()

/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:1: DeprecationWarning: Using Nominatim with the default "geopy/1.20.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  """Entry point for launching an IPython kernel.
/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:4: DeprecationWarning: `timeout=None` has been passed to a geocoder call. Using default geocoder timeout. In geopy 2.0 the behavior will be different: None will mean "no timeout" instead of "default geocoder timeout". Pass geopy.geocoders.base.DEFAULT_SENTINEL instead of None to get rid of this warning.
  after removing the cwd from sys.path.


(33, 3)


borough   Latitude  Longitude
0        City of London  51.515618  -0.091998
1  Barking and Dagenham  51.554117   0.150504
2                Barnet  51.648784  -0.172913
3                Bexley  51.441679   0.150488
4                 Brent  51.441837   0.234833

In [19]:
address = 'London'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of London are {}, {}.'.format(latitude, longitude))

map_London = folium.Map(location=[latitude, longitude], zoom_start=10)

for borough, lat, lng in zip( borough_df['borough'], borough_df['Latitude'], borough_df['Longitude']):
    label = '{}'.format(borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=2,
        popup=label,
        color='red',
        fill=True,
        fill_color='#0000ff',
        fill_opacity=0.7,
        parse_html=False).add_to(map_London)


folium.GeoJson(borough_geo,
              ).add_to(map_London)

map_London

/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.20.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  This is separate from the ipykernel package so we can avoid doing imports until


The geograpical coordinate of London are 51.5073219, -0.1276474.


# Considering the elderly population of London

In [20]:
age_df = pd.read_csv("age_data.csv")
age_df.columns = ['borough','Population 50+','50+','Female50+','Male 50+','Population 65+']
age_df.head()

borough  Population 50+  50+  Female50+  Male 50+  \
0  Barking and Dagenham           43700   24         54        46   
1                Barnet          102700   29         54        46   
2                Bexley           77800   34         54        46   
3                 Brent           77800   25         52        48   
4               Bromley          108200   35         54        46   

   Population 65+  
0           19200  
1           47400  
2           47900  
3           32600  
4           51900

In [21]:
age_loc_df = borough_df.merge(age_df,on='borough')


In [22]:
age_loc_df.head()


borough   Latitude  Longitude  Population 50+  50+  Female50+  \
0        City of London  51.515618  -0.091998            2400   32         50   
1  Barking and Dagenham  51.554117   0.150504           43700   24         54   
2                Barnet  51.648784  -0.172913          102700   29         54   
3                Bexley  51.441679   0.150488           77800   34         54   
4                 Brent  51.441837   0.234833           77800   25         52   

   Male 50+  Population 65+  
0        50            1000  
1        46           19200  
2        46           47400  
3        46           47900  
4        48           32600

In [23]:
# set number of clusters
kclusters = 4

age_grouped_clustering = age_loc_df[['Population 65+',
                                  'Latitude',
                                  'Longitude']]

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(age_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([3, 1, 2, 2, 0, 2, 1, 2, 0, 0], dtype=int32)

In [24]:
age_loc_df['Cluster Labels'] = kmeans.labels_
age_loc_df.head()


borough   Latitude  Longitude  Population 50+  50+  Female50+  \
0        City of London  51.515618  -0.091998            2400   32         50   
1  Barking and Dagenham  51.554117   0.150504           43700   24         54   
2                Barnet  51.648784  -0.172913          102700   29         54   
3                Bexley  51.441679   0.150488           77800   34         54   
4                 Brent  51.441837   0.234833           77800   25         52   

   Male 50+  Population 65+  Cluster Labels  
0        50            1000               3  
1        46           19200               1  
2        46           47400               2  
3        46           47900               2  
4        48           32600               0

In [25]:
address = 'London, England'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=10)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for bor, lat, lon, cluster in zip(age_loc_df['borough'],age_loc_df['Latitude'], age_loc_df['Longitude'], age_loc_df['Cluster Labels']):
    label = folium.Popup(bor + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
    
folium.GeoJson(borough_geo,
              ).add_to(map_clusters)


map_clusters

/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.20.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  This is separate from the ipykernel package so we can avoid doing imports until


In [26]:
age_loc_df_clustered = age_loc_df.groupby('Cluster Labels').mean().reset_index()
age_loc_df_clustered

Cluster Labels   Latitude  Longitude  Population 50+        50+  Female50+  \
0               0  51.553698  -0.148597    79800.000000  27.500000  53.333333   
1               1  51.500836  -0.003533    53333.333333  23.380952  53.523810   
2               2  51.466143  -0.027392    98050.000000  31.750000  54.000000   
3               3  51.515618  -0.091998     2400.000000  32.000000  50.000000   

    Male 50+  Population 65+  
0  46.666667    35016.666667  
1  46.952381    22419.047619  
2  46.000000    47925.000000  
3  50.000000     1000.000000

## Observation

#### From the grouped dataframe, we can see that certain clusters have a lower proportion of elderly populatoin, compared to other clusters.
#### In general, as the cluster label increases, the proportion of elderly people increases.
#### Establishing a hospital in a borough with more elderly people is advantageous

In [27]:
# Obtaining the cluster with the highest proportion of elderly patients

opt_k_eld = age_loc_df_clustered.sort_values('Population 65+', ascending=False).iloc[0]['Cluster Labels']
opt_k_eld

2.0

In [28]:
opt_loc_eld = age_loc_df[age_loc_df['Cluster Labels'] == opt_k_eld]
opt_loc_eld

borough   Latitude  Longitude  Population 50+  50+  Female50+  Male 50+  \
2   Barnet  51.648784  -0.172913          102700   29         54        46   
3   Bexley  51.441679   0.150488           77800   34         54        46   
5  Bromley  51.402805   0.014814          108200   35         54        46   
7  Croydon  51.371305  -0.101957          103500   29         54        46   

   Population 65+  Cluster Labels  
2           47400               2  
3           47900               2  
5           51900               2  
7           44500               2

# Considering the crime rates in London

### These boroughs are potential locations for our new hospital. Now, we consider our second criteria - crime.
### We want to build a hospital in as safe a place as possible.

In [29]:
crime_df = pd.read_csv("crime rates.csv")
crime_df.columns = ['Code','borough','Year','Offences','Rate','Number_of_offences']
crime_df.head()

Code               borough     Year               Offences   Rate  \
0  E09000002  Barking and Dagenham  1999-00  All recorded offences  120.5   
1  E09000003                Barnet  1999-00  All recorded offences   98.0   
2  E09000004                Bexley  1999-00  All recorded offences   95.1   
3  E09000005                 Brent  1999-00  All recorded offences  127.7   
4  E09000006               Bromley  1999-00  All recorded offences   89.8   

  Number_of_offences  
0             19,567  
1             30,708  
2             20,680  
3             33,253  
4             26,474

In [30]:
crime_loc_df = borough_df.merge(crime_df,on='borough')
crime_loc_df.Number_of_offences = [(int)(a.replace(',', '')) for a in crime_loc_df.Number_of_offences.values]


In [31]:
crime_loc_df.head()


borough   Latitude  Longitude       Code     Year  \
0  Barking and Dagenham  51.554117   0.150504  E09000002  1999-00   
1  Barking and Dagenham  51.554117   0.150504  E09000002  2000-01   
2  Barking and Dagenham  51.554117   0.150504  E09000002  2001-02   
3  Barking and Dagenham  51.554117   0.150504  E09000002  2002-03   
4  Barking and Dagenham  51.554117   0.150504  E09000002  2003-04   

                Offences   Rate  Number_of_offences  
0  All recorded offences  120.5               19567  
1  All recorded offences  123.6               20253  
2  All recorded offences  124.0               20538  
3  All recorded offences  122.6               20394  
4  All recorded offences  133.2               22144

In [32]:
crime_loc_df = crime_loc_df.groupby('borough').mean().reset_index()


In [33]:
crime_loc_df


borough   Latitude  Longitude       Rate  \
0     Barking and Dagenham  51.554117   0.150504  21.952778   
1                   Barnet  51.648784  -0.172913  16.923889   
2                   Bexley  51.441679   0.150488  14.442778   
3                    Brent  51.441837   0.234833  20.954444   
4                  Bromley  51.402805   0.014814  16.421667   
5                   Camden  51.542304  -0.139560  36.738889   
6                  Croydon  51.371305  -0.101957  18.808889   
7                   Ealing  51.512655  -0.305195  20.957778   
8                  Enfield  51.652085  -0.081017  17.282778   
9                Greenwich  52.036732   1.168934  22.347222   
10                 Hackney  51.543240  -0.049362  28.242222   
11  Hammersmith and Fulham  51.492038  -0.223640  28.006111   
12                Haringey  51.587930  -0.105410  24.864444   
13                  Harrow  51.596769  -0.337275  13.680000   
14                Havering  51.035863  -2.841754  15.923333   
15              Hillingdon  51.542519  -0.448335  19.147222   
16                Hounslow  51.468613  -0.361347  21.651111   
17               Islington  51.538429  -0.099905  33.258889   
18  Kensington and Chelsea  51.498995  -0.199123  29.980000   
19    Kingston upon Thames  51.409628  -0.306262  15.887778   
20                 Lambeth  51.501301  -0.117287  28.433333   
21                Lewisham  51.462433  -0.010133  21.325556   
22                  Merton  51.410803  -0.188098  15.618333   
23                  Newham  51.530000   0.029318  25.265556   
24               Redbridge  51.576320   0.045410  18.231667   
25    Richmond upon Thames  51.440354  -0.308151  14.341667   
26               Southwark  51.502922  -0.103458  28.026667   
27                  Sutton  51.357511  -0.173640  14.370556   
28           Tower Hamlets  51.128863   1.298669  27.683889   
29          Waltham Forest  51.556999  -0.005835  21.985556   
30              Wandsworth  51.457027  -0.193261  19.602778   
31             Westminster  51.497321  -0.137149  62.828889   

    Number_of_offences  
0          3853.844444  
1          5728.666667  
2          3261.266667  
3          6014.255556  
4          5002.144444  
5          7772.544444  
6          6577.155556  
7          6727.477778  
8          5104.055556  
9          5302.955556  
10         6398.644444  
11         4878.555556  
12         5935.277778  
13         3084.511111  
14         3700.533333  
15         5012.750000  
16         5069.611111  
17         6394.611111  
18         4798.116667  
19         2473.683333  
20         8167.438889  
21         5668.150000  
22         3041.705556  
23         6950.083333  
24         4776.827778  
25         2614.144444  
26         7626.333333  
27         2678.411111  
28         6342.477778  
29         5265.427778  
30         5654.100000  
31        13520.216667

In [34]:
kclusters = 4

crime_grouped_clustering = crime_loc_df[['Rate',
                                  'Latitude',
                                  'Longitude']]

kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(crime_grouped_clustering)

kmeans.labels_[0:10]

array([3, 0, 0, 3, 0, 2, 3, 3, 0, 3], dtype=int32)

In [35]:
crime_loc_df['Cluster Labels'] = kmeans.labels_
crime_loc_df.head()

borough   Latitude  Longitude       Rate  Number_of_offences  \
0  Barking and Dagenham  51.554117   0.150504  21.952778         3853.844444   
1                Barnet  51.648784  -0.172913  16.923889         5728.666667   
2                Bexley  51.441679   0.150488  14.442778         3261.266667   
3                 Brent  51.441837   0.234833  20.954444         6014.255556   
4               Bromley  51.402805   0.014814  16.421667         5002.144444   

   Cluster Labels  
0               3  
1               0  
2               0  
3               3  
4               0

In [36]:
crime_clustered = crime_loc_df.groupby('Cluster Labels').mean().reset_index()
crime_clustered


Cluster Labels   Latitude  Longitude       Rate  Number_of_offences
0               0  51.452055  -0.381673  15.738586         3769.631818
1               1  51.497321  -0.137149  62.828889        13520.216667
2               2  51.468512   0.045792  30.046250         6547.340278
3               3  51.543514   0.004343  21.571944         5669.257407

### From the grouped dataframe, we see that the number of offences taking place is least in cluster 0

### This shows that a borough in certain clusters are the safer than others, to establish our new hospital.

In [37]:
# Obtaining the cluster with the highest proportion of elderly patients

opt_k_safe = crime_clustered.sort_values('Rate').iloc[0]['Cluster Labels']
opt_k_safe

0.0

In [38]:
safe_loc = crime_loc_df[crime_loc_df['Cluster Labels']==opt_k_safe]
safe_loc

borough   Latitude  Longitude       Rate  Number_of_offences  \
1                 Barnet  51.648784  -0.172913  16.923889         5728.666667   
2                 Bexley  51.441679   0.150488  14.442778         3261.266667   
4                Bromley  51.402805   0.014814  16.421667         5002.144444   
8                Enfield  51.652085  -0.081017  17.282778         5104.055556   
13                Harrow  51.596769  -0.337275  13.680000         3084.511111   
14              Havering  51.035863  -2.841754  15.923333         3700.533333   
19  Kingston upon Thames  51.409628  -0.306262  15.887778         2473.683333   
22                Merton  51.410803  -0.188098  15.618333         3041.705556   
24             Redbridge  51.576320   0.045410  18.231667         4776.827778   
25  Richmond upon Thames  51.440354  -0.308151  14.341667         2614.144444   
27                Sutton  51.357511  -0.173640  14.370556         2678.411111   

    Cluster Labels  
1                0  
2                0  
4                0  
8                0  
13               0  
14               0  
19               0  
22               0  
24               0  
25               0  
27               0

In [39]:
address = 'London, England'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=10)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for bor, lat, lon, cluster in zip(crime_loc_df['borough'],crime_loc_df['Latitude'], crime_loc_df['Longitude'], crime_loc_df['Cluster Labels']):
    label = folium.Popup(bor + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)

folium.GeoJson(borough_geo,
              ).add_to(map_clusters)
    
map_clusters

/usr/local/lib/python3.7/site-packages/ipykernel_launcher.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.20.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  This is separate from the ipykernel package so we can avoid doing imports until


## Finally, we consider an important factor - whether or not a hospital already exists in the location we are planning to build a new hospital.

### For this, we require the FourSquar API.

In [40]:
CLIENT_ID = 'KIDZBR1G0WK3DDCJF1HF1VRL2B0UIOXOFVUXRBHTPA023QXR' # your Foursquare ID
CLIENT_SECRET = 'EM5TMCK3MPTS4EHQHKJONMXH0NMEH5ABUHOWZOQIWH5OJPPN' # your Foursquare Secret
VERSION = '20190826' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: KIDZBR1G0WK3DDCJF1HF1VRL2B0UIOXOFVUXRBHTPA023QXR
CLIENT_SECRET:EM5TMCK3MPTS4EHQHKJONMXH0NMEH5ABUHOWZOQIWH5OJPPN


### We define a function to find all the hospitals present within a 1000km radius of each borough's latitude and longitude.

(This is upper-limited at 100)

In [41]:
category_id = "4bf58dd8d48988d196941735"
LIMIT = 100

def getNearbyHospitals(names, latitudes, longitudes, radius=1000):

    hospitals_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)

        # create the API request URL
        url= "https://api.foursquare.com/v2/venues/search?ll={},{}&categoryId={}&client_id={}&client_secret={}&radius={}&limit={}&v={}".format(
        lat,
        lng,
        category_id,
        CLIENT_ID,
        CLIENT_SECRET,
        radius,
        LIMIT,
        VERSION
        )

        # make the GET request
        results = requests.get(url).json()['response']['venues']

        # return only relevant information for each nearby hospital
        hospitals_list.append([(
            name,
            lat,
            lng,
            v['name'],
            v['location']['lat'],
            v['location']['lng']) for v in results])

    nearby_hospitals = pd.DataFrame([item for hospital_list in hospitals_list for item in hospital_list])
    nearby_hospitals.columns = ['Borough',
                  'Borough Latitude',
                  'Borough Longitude',
                  'Hospital',
                  'Hospital Latitude',
                  'Hospital Longitude']

    return(nearby_hospitals)

In [ ]:
London_hospitals = getNearbyHospitals(names=borough_df['borough'],
                                   latitudes=borough_df['Latitude'],
                                   longitudes=borough_df['Longitude']
                                )


In [ ]:
London_hospitals.head()


In [ ]:
London_hospitals.groupby('Borough').count().max()['Hospital']


### We see that the max number of nearby hospitals is 33.

### Grouping the dataframe, based on unique hospital names, and taking the centroid of the co-ordinates:

In [ ]:
London_hosp_cluster = pd.DataFrame(London_hospitals.groupby('Hospital').mean().reset_index())


In [ ]:
London_hosp_cluster.head()


### By observation, we see that the closest, well-known hospitals in London are all centered within the limits of the City of London borough.

## Visualisation of the 19 hospitals already present (bright red spots):

In [ ]:
address = 'City of London, England'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

borough_geo = 'london_boroughs_proper.geojson'
address = 'London'

print('The geograpical coordinate of London are {}, {}.'.format(latitude, longitude))

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=10)

for ven, lat, lon in zip(London_hosp_cluster['Hospital'],London_hosp_cluster['Hospital Latitude'], London_hosp_cluster['Hospital Longitude']):
    label = folium.Popup(str(ven), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='red',
        fill_opacity=0.7).add_to(map_clusters)

folium.GeoJson(borough_geo).add_to(map_clusters)

In [ ]:
map_clusters

From the visualisation of the map of London, we see that the existing hospitals are clustered toward the center, concentrated around the borough of the City of London. 

So, that eliminates the City of London and neighboring boroughs as potential locations.

Instead, we consider the initial two criteria : Proportion of elderly patients and crime rate

In [42]:
opt_loc_eld

borough   Latitude  Longitude  Population 50+  50+  Female50+  Male 50+  \
2   Barnet  51.648784  -0.172913          102700   29         54        46   
3   Bexley  51.441679   0.150488           77800   34         54        46   
5  Bromley  51.402805   0.014814          108200   35         54        46   
7  Croydon  51.371305  -0.101957          103500   29         54        46   

   Population 65+  Cluster Labels  
2           47400               2  
3           47900               2  
5           51900               2  
7           44500               2

In [43]:
safe_loc

borough   Latitude  Longitude       Rate  Number_of_offences  \
1                 Barnet  51.648784  -0.172913  16.923889         5728.666667   
2                 Bexley  51.441679   0.150488  14.442778         3261.266667   
4                Bromley  51.402805   0.014814  16.421667         5002.144444   
8                Enfield  51.652085  -0.081017  17.282778         5104.055556   
13                Harrow  51.596769  -0.337275  13.680000         3084.511111   
14              Havering  51.035863  -2.841754  15.923333         3700.533333   
19  Kingston upon Thames  51.409628  -0.306262  15.887778         2473.683333   
22                Merton  51.410803  -0.188098  15.618333         3041.705556   
24             Redbridge  51.576320   0.045410  18.231667         4776.827778   
25  Richmond upon Thames  51.440354  -0.308151  14.341667         2614.144444   
27                Sutton  51.357511  -0.173640  14.370556         2678.411111   

    Cluster Labels  
1                0  
2                0  
4                0  
8                0  
13               0  
14               0  
19               0  
22               0  
24               0  
25               0  
27               0

In [45]:

ideal_locations = opt_loc_eld.merge(safe_loc,on='borough')
ideal_locations = ideal_locations[['borough','Latitude_x','Longitude_x','Rate','Population 65+']]

ideal_locations

borough  Latitude_x  Longitude_x       Rate  Population 65+
0   Barnet   51.648784    -0.172913  16.923889           47400
1   Bexley   51.441679     0.150488  14.442778           47900
2  Bromley   51.402805     0.014814  16.421667           51900

In [ ]:
address = 'London, England'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

borough_geo = 'london_boroughs_proper.geojson'
address = 'London'

print('The geograpical coordinate of London are {}, {}.'.format(latitude, longitude))

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=10)

for ven, lat, lon in zip(ideal_locations['borough'],ideal_locations['Latitude_x'], ideal_locations['Longitude_x']):
    label = folium.Popup(str(ven), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='red',
        fill_opacity=0.7).add_to(map_clusters)
    print(ven)

folium.GeoJson(borough_geo).add_to(map_clusters)

map_clusters

## Thus using techniques of data analysis, visualisation tools like folium and APIs like FourSquare, I have identified 3 potential locations where it will be best suited to build a hospital for the elderly.